In [1]:
import os
import numpy as np
import pandas as pd
import cv2
import json
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import TimeDistributed, Conv2D, MaxPooling2D, Flatten, LSTM, Dense
from tensorflow.keras.callbacks import EarlyStopping

c:\Users\pedro\anaconda3\envs\new_pdi\lib\site-packages\h5py\__init__.py:36: UserWarning: h5py is running against HDF5 1.14.5 when it was built against 1.14.6, this may cause problems
  _warn(("h5py is running against HDF5 {0} when it was built against {1}, "


In [ ]:
# --- Configurações de Caminho (Ajuste conforme sua estrutura de diretórios) ---
CAMINHO_BASE = '..'
DATA_DIR = os.path.join(CAMINHO_BASE, 'UnityEyes_Windows','UnityEyes_Windows','imgs', 'imgs')
LABELS_FILE = os.path.join('..', 'output', 'gaze_labels.csv')
# Use o mesmo diretório onde você salvou os lotes
output_dir_sequences = 'processed_sequences'
MODELO_SALVO = os.path.join(CAMINHO_BASE, 'models', 'gaze_attention_model.keras')

In [3]:
IMG_SIZE = (64, 64) # Tamanho da imagem redimensionada
TIME_WINDOW = 10 # Número de frames por sequência

In [4]:
# --- 1. Carregar os rótulos do arquivo CSV ---
print("Carregando o arquivo de rótulos...")
try:
    labels_df = pd.read_csv(LABELS_FILE)
    print("CSV de rótulos carregado com sucesso!")
except FileNotFoundError:
    print(f"Erro: O arquivo de rótulos '{LABELS_FILE}' não foi encontrado. Verifique o caminho.")
    exit()

Carregando o arquivo de rótulos...
CSV de rótulos carregado com sucesso!


In [ ]:
# --- 2. Carregar e pré-processar as imagens associadas aos rótulos ---
print("Carregando e pré-processando as imagens...")
all_images = []
all_labels = []

if not os.path.exists(DATA_DIR):
    print(f"Erro: O diretório de imagens '{DATA_DIR}' não foi encontrado.")
else:
    for index, row in labels_df.iterrows():
        image_filename = row['image_filename']
        file_path = os.path.join(DATA_DIR, image_filename)
        # Verifica se o arquivo de imagem existe
        print(f"Processando imagem: {file_path}")
        
        # Lê a imagem e pré-processa se o arquivo existir
        if os.path.exists(file_path):
            img = cv2.imread(file_path)
            if img is not None:
                img_resized = cv2.resize(img, IMG_SIZE)
                img_normalized = img_resized.astype('float32') / 255.0
                all_images.append(img_normalized)
                all_labels.append(row['attention'])

    images_array = np.array(all_images)
    labels_array = np.array(all_labels)

    print(f"Pré-processamento concluído. {len(images_array)} imagens processadas.")

    if len(images_array) == 0:
        print("Nenhuma imagem foi processada. Verifique se o caminho do diretório 'DATA_DIR' está correto e se as imagens existem.")
        exit()

Carregando e pré-processando as imagens...
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\1.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\10.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\1000.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\10000.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100000.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100001.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100002.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100003.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100004.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100005.jpg
Processando imagem: ..\UnityEyes_Windows\UnityEyes_Windows\imgs\imgs\100006.jpg
Processando 

In [ ]:
# --- 3. Agrupar em sequências e salvar em lotes ---
print("Criando sequências de dados em lotes...")

# Define o tamanho do lote para a criação das sequências.
# Um valor de 1000 a 5000 é um bom ponto de partida.
BATCH_SIZE_SEQUENCE = 2000

# Caminho para salvar os arquivos de sequência temporários
output_dir_sequences = 'processed_sequences'
if not os.path.exists(output_dir_sequences):
    os.makedirs(output_dir_sequences)

# Armazena os dados do lote atual
current_batch_data = []
current_batch_labels = []
batch_counter = 0

for i in range(len(images_array) - TIME_WINDOW + 1):
    sequence_images = images_array[i:i + TIME_WINDOW]
    window_labels = labels_array[i:i + TIME_WINDOW]
    
    sequence_label = 1 if np.mean(window_labels) > 0.5 else 0

    current_batch_data.append(sequence_images)
    current_batch_labels.append(sequence_label)

    # Quando o lote atual atingir o tamanho definido, salve-o
    if len(current_batch_data) == BATCH_SIZE_SEQUENCE or i == (len(images_array) - TIME_WINDOW):
        print(f"Salvando lote {batch_counter} com {len(current_batch_data)} amostras.")
        
        X_batch = np.array(current_batch_data)
        y_batch = np.array(current_batch_labels)

        # Salve os arrays em arquivos .npy
        np.save(os.path.join(output_dir_sequences, f'X_batch_{batch_counter}.npy'), X_batch)
        np.save(os.path.join(output_dir_sequences, f'y_batch_{batch_counter}.npy'), y_batch)

        # Limpe a memória para o próximo lote
        current_batch_data = []
        current_batch_labels = []
        batch_counter += 1

print(f"Processamento em lotes concluído. {batch_counter} lotes criados.")

In [ ]:
# --- 4. Gerador de Dados para o Treinamento ---
def data_generator(data_files, batch_size):
    """
    Função geradora para carregar dados em lotes para o treinamento.
    """
    total_files = len(data_files)
    file_indices = np.arange(total_files)
    
    while True:
        # Embaralha a ordem de leitura dos lotes a cada época
        np.random.shuffle(file_indices)
        
        for i in file_indices:
            X_batch = np.load(os.path.join(output_dir_sequences, f'X_batch_{i}.npy'))
            y_batch = np.load(os.path.join(output_dir_sequences, f'y_batch_{i}.npy'))
            
            # Use train_test_split para dividir cada lote em treino/validação/teste
            X_train, X_temp, y_train, y_temp = train_test_split(X_batch, y_batch, test_size=0.3, random_state=42)
            X_val, X_test, y_val, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=42)
            
            # O 'yield' transforma a função em um gerador
            yield X_train, y_train



In [ ]:
# --- Carregar a lista de lotes ---
batch_files = sorted([f for f in os.listdir(output_dir_sequences) if f.startswith('X_batch_')])
total_batches = len(batch_files)

In [ ]:
# Dividir os lotes em treino, validação e teste
batch_indices = np.arange(total_batches)
train_batches, test_batches = train_test_split(batch_indices, test_size=0.2, random_state=42)
val_batches, test_batches = train_test_split(test_batches, test_size=0.5, random_state=42)

print(f"Total de lotes: {total_batches}")
print(f"Lotes para treino: {len(train_batches)}, para validação: {len(val_batches)}, para teste: {len(test_batches)}")


In [ ]:
# --- 5. Construir o modelo CNN-LSTM ---
print("\nConstruindo o modelo CNN-LSTM...")
# Carregue o primeiro lote para obter as dimensões dos dados de entrada
X_sample = np.load(os.path.join(output_dir_sequences, f'X_batch_{train_batches[0]}.npy'))
input_shape = X_sample.shape[1:]

model = Sequential([
    TimeDistributed(Conv2D(32, (3, 3), activation='relu'), input_shape=input_shape),
    TimeDistributed(MaxPooling2D((2, 2))),
    TimeDistributed(Conv2D(64, (3, 3), activation='relu')),
    TimeDistributed(MaxPooling2D((2, 2))),
    TimeDistributed(Flatten()),

    LSTM(64),
    Dense(1, activation='sigmoid')
])

In [ ]:
# --- 6. Compilar e treinar o modelo ---
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

model.summary()

print("\nIniciando o treinamento do modelo...")
callback = EarlyStopping(monitor='val_loss', patience=3)

In [ ]:
# Use os geradores para alimentar o modelo
history = model.fit(
    data_generator(train_batches, batch_size=32), # Gerador para dados de treino
    steps_per_epoch=len(train_batches),
    epochs=10,
    validation_data=data_generator(val_batches, batch_size=32), # Gerador para dados de validação
    validation_steps=len(val_batches),
    callbacks=[callback]
)


In [ ]:
# --- 7. Avaliar o modelo ---
print("\nAvaliando o modelo...")
# A avaliação também será feita com um gerador
loss, accuracy = model.evaluate(data_generator(test_batches, batch_size=32), steps=len(test_batches))
print(f"Acurácia final do modelo: {accuracy:.4f}")

In [ ]:
# --- 8. Salvar o modelo treinado ---
model_path = os.path.join(CAMINHO_BASE, 'models', 'gaze_attention_model.keras')
model.save(model_path)
print(f"\nModelo salvo em: {model_path}")